# Initializing the environment and clusters

In [1]:
import ipyparallel as ipp
c = ipp.Client()
dview = c[:]

In [2]:
%%px --local
import sys
sys.path.append("/home/sac086/wisdm_model_personalization/")
import warnings
import os
from wisdm import wisdm
import numpy as np
import pandas as pd

from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold, StratifiedKFold, StratifiedShuffleSplit, ShuffleSplit
from sklearn.cluster import KMeans
from scipy.stats import mode
from collections import Counter
import time

In [3]:
from wisdm import viz
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from plotly.graph_objs import *

In [3]:
%%px --local
from imp import reload
reload(wisdm)

<module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[0:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[1:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[2:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[3:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

...

Out[22:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[23:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[24:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[25:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

Out[26:2]: <module 'wisdm.wisdm' from '/home/sac086/wisdm_model_personalization/wisdm/wisdm.py'>

# Experiment #1

In [4]:
description = '''
Training set = WISDM v1.1
Test Set = WISDM v1.1
validation = leave-one user out, class label stratified 10-fold cross-validation within user where the training folds
are used as the pool from which we can actively sample
Sampling Methods = Least-Certain Sampling, Random Sampling
Modeling Methods = Impersonal, Sampled Personal, Sampled Personal data + All Impersonal Data, 
                    Sampled Personal Data + nearest cluster of Impersonal data,
                    Sampled Personal Data + Impersonal Data selected and weighted with Garcia-Ceja approach
'''

In [5]:
%%px --local
experiment_name1 = "experiment_09-05_train_v1_with_random_and_least_certain/"
experiment_output_path1 = "/home/sac086/wisdm_model_personalization/results/" + experiment_name1

In [6]:
if not os.path.exists(experiment_output_path1):
    os.makedirs(experiment_output_path1)
with open(experiment_output_path1 + "README.md", "w") as fOut:
    fOut.write(description)

In [7]:
wisdm.set_data(version="1")

In [8]:
command1 = """wisdm.pipeline1('1', '%s', user_ids, minimum_personal_samples=110)""" % experiment_output_path1

In [10]:
# divide the user ids up among the different cores
scatter_result = dview.scatter("user_ids", wisdm.user_ids[:3])
start = time.time()
dview.block = True
results = dview.execute(command1)
finish = time.time()
print("Finished all models in %s minutes" % ((finish - start) / 60.))

Finished all models in 17.87161591053009 minutes


### Experiment #1 Results


In [56]:
viz.set_data(version="1")

In [62]:
experiment_output_path1

'/home/sac086/wisdm_model_personalization/results/experiment_09-02_train_v1_with_random_and_least_certain/'

In [63]:
results_df = viz.get_results_dataframe(experiment_output_path1)

Loading results from /home/sac086/wisdm_model_personalization/results/experiment_09-02_train_v1_with_random_and_least_certain/
36 users loaded, 0 users excluded
These users may not have had enough data:
[]


In [64]:
viz.set_data(version="1")
fig = viz.accuracy_means_by_training_size()
iplot(fig)

In [65]:
fig = viz.plotUserBests()
fig.layout['title'] = "# of users whose best performance came from a particular approach"
iplot(fig)

# Experiment 2

In [67]:
description = '''
Training set = WISDM v2.0
Test Set = WISDM v2.0
validation = leave-one user out, class label stratified 10-fold cross-validation within user where the training folds
are used as the pool from which we can actively sample
Sampling Methods = Least-Certain Sampling, Random Sampling
Modeling Methods = Impersonal, Sampled Personal, Sampled Personal data + All Impersonal Data, 
                    Sampled Personal Data + nearest cluster of Impersonal data,
                    Sampled Personal Data + Impersonal Data selected and weighted with Garcia-Ceja approach
'''

In [68]:
%%px --local
experiment_name2 = "experiment_09-03_train_v2_with_random_and_least_certain/"
experiment_output_path2 = "/home/sac086/wisdm_model_personalization/results/" + experiment_name2

In [69]:
if not os.path.exists(experiment_output_path2):
    os.makedirs(experiment_output_path2)
with open(experiment_output_path2 + "README.md", "w") as fOut:
    fOut.write(description)

In [70]:
# check for existing user_ids
finished_experiment_ids = [f.split(".")[0] for f in os.listdir(experiment_output_path2) if ".pickle" in f]
finished_experiment_ids

['194',
 '1274',
 '1559',
 '1319',
 '1512',
 '1117',
 '1320',
 '1253',
 '1104',
 '1758',
 '1809',
 '1238',
 '1703',
 '1707',
 '1778',
 '1799',
 '1774',
 '1742',
 '1246',
 '998',
 '1477',
 '1759',
 '1775',
 '1793',
 '1676',
 '1603']

In [19]:
wisdm.set_data(version="2", make_compatible=True)

In [23]:
user_ids = [user_id for user_id in wisdm.user_ids if user_id not in finished_experiment_ids]

In [71]:
command = """wisdm.pipeline1('2', '%s', user_ids)""" % experiment_output_path2

In [24]:
scatter_result = dview.scatter("user_ids", user_ids)
start = time.time()
dview.block = True
results = dview.execute(command)
finish = time.time()
print("Finished all models in %s minutes" % ((finish - start) / 60.))

Finished all models in 9.920355089505513 minutes


In [10]:
# just for testing the pipeline
user_ids = [wisdm.user_ids[0]]
start = time.time()
wisdm.pipeline1('2', experiment_output_path2, user_ids)
finish = time.time()
print("Finished all models in %s minutes" % ((finish - start) / 60.))

Running user #0: 194
168 personal samples
	Running Fold #0

	amount of personal data : 10 row
	random personal model score : M=0.789, SD=0.115
	impersonal model score : M=0.632
	random personal + ALL Impersonal : M=0.800, SD=0.052
	random personal + CLUSTER Impersonal : M=0.895, SD=0.137
	least_certain personal model score : 0.684
	least_certain personal + ALL Impersonal : 0.526
	least_certain personal + CLUSTER Impersonal : 0.579


	amount of personal data : 20 row
	random personal model score : M=0.832, SD=0.084
	impersonal model score : M=0.632
	random personal + ALL Impersonal : M=0.832, SD=0.061
	random personal + CLUSTER Impersonal : M=0.926, SD=0.098
	least_certain personal model score : 0.684
	least_certain personal + ALL Impersonal : 0.789
	least_certain personal + CLUSTER Impersonal : 0.947


	amount of personal data : 30 row
	random personal model score : M=0.884, SD=0.084
	impersonal model score : M=0.632
	random personal + ALL Impersonal : M=0.926, SD=0.079
	random persona

	amount of personal data : 30 row
	random personal model score : M=0.922, SD=0.044
	impersonal model score : M=0.667
	random personal + ALL Impersonal : M=0.833, SD=0.093
	random personal + CLUSTER Impersonal : M=0.922, SD=0.044
	least_certain personal model score : 0.722
	least_certain personal + ALL Impersonal : 0.667
	least_certain personal + CLUSTER Impersonal : 0.722


	amount of personal data : 40 row
	random personal model score : M=0.933, SD=0.042
	impersonal model score : M=0.667
	random personal + ALL Impersonal : M=0.878, SD=0.065
	random personal + CLUSTER Impersonal : M=0.933, SD=0.054
	least_certain personal model score : 0.722
	least_certain personal + ALL Impersonal : 0.667
	least_certain personal + CLUSTER Impersonal : 0.722


	amount of personal data : 50 row
	random personal model score : M=0.922, SD=0.044
	impersonal model score : M=0.667
	random personal + ALL Impersonal : M=0.889, SD=0.079
	random personal + CLUSTER Impersonal : M=0.933, SD=0.042
	least_certain pe

	amount of personal data : 50 row
	random personal model score : M=0.965, SD=0.029
	impersonal model score : M=0.647
	random personal + ALL Impersonal : M=0.776, SD=0.044
	random personal + CLUSTER Impersonal : M=0.976, SD=0.029
	least_certain personal model score : 0.765
	least_certain personal + ALL Impersonal : 0.765
	least_certain personal + CLUSTER Impersonal : 0.647


	amount of personal data : 60 row
	random personal model score : M=1.000, SD=0.000
	impersonal model score : M=0.647
	random personal + ALL Impersonal : M=0.776, SD=0.024
	random personal + CLUSTER Impersonal : M=1.000, SD=0.000
	least_certain personal model score : 0.765
	least_certain personal + ALL Impersonal : 0.765
	least_certain personal + CLUSTER Impersonal : 0.824


	amount of personal data : 70 row
	random personal model score : M=1.000, SD=0.000
	impersonal model score : M=0.647
	random personal + ALL Impersonal : M=0.776, SD=0.024
	random personal + CLUSTER Impersonal : M=1.000, SD=0.000
	least_certain pe

	amount of personal data : 70 row
	random personal model score : M=0.938, SD=0.000
	impersonal model score : M=0.250
	random personal + ALL Impersonal : M=0.750, SD=0.056
	random personal + CLUSTER Impersonal : M=0.938, SD=0.000
	least_certain personal model score : 0.750
	least_certain personal + ALL Impersonal : 0.625
	least_certain personal + CLUSTER Impersonal : 0.750


	amount of personal data : 80 row
	random personal model score : M=0.938, SD=0.000
	impersonal model score : M=0.250
	random personal + ALL Impersonal : M=0.750, SD=0.068
	random personal + CLUSTER Impersonal : M=0.950, SD=0.025
	least_certain personal model score : 0.750
	least_certain personal + ALL Impersonal : 0.625
	least_certain personal + CLUSTER Impersonal : 0.688


	amount of personal data : 90 row
	random personal model score : M=0.912, SD=0.031
	impersonal model score : M=0.250
	random personal + ALL Impersonal : M=0.750, SD=0.068
	random personal + CLUSTER Impersonal : M=0.938, SD=0.000
	least_certain pe

	amount of personal data : 90 row
	random personal model score : M=0.988, SD=0.025
	impersonal model score : M=0.312
	random personal + ALL Impersonal : M=0.850, SD=0.050
	random personal + CLUSTER Impersonal : M=0.963, SD=0.031
	least_certain personal model score : 0.812
	least_certain personal + ALL Impersonal : 0.875
	least_certain personal + CLUSTER Impersonal : 0.750


	amount of personal data : 100 row
	random personal model score : M=1.000, SD=0.000
	impersonal model score : M=0.312
	random personal + ALL Impersonal : M=0.838, SD=0.085
	random personal + CLUSTER Impersonal : M=0.975, SD=0.031
	least_certain personal model score : 0.938
	least_certain personal + ALL Impersonal : 0.812
	least_certain personal + CLUSTER Impersonal : 0.938


sample_experiments took 0.8845106879870097 minutes
	Running Fold #9

	amount of personal data : 10 row
	random personal model score : M=0.773, SD=0.213
	impersonal model score : M=0.333
	random personal + ALL Impersonal : M=0.573, SD=0.172
	rand

### Experiment #2 Results

In [72]:
from wisdm import viz

In [74]:
viz.set_data(version="2")

In [75]:
results_df = viz.get_results_dataframe(experiment_output_path2)

Loading results from /home/sac086/wisdm_model_personalization/results/experiment_09-03_train_v2_with_random_and_least_certain/
26 users loaded, 28 users excluded
These users may not have had enough data:
['1097', '1205', '1247', '1269', '1276', '1277', '1280', '1480', '1491', '1511', '1518', '1531', '1554', '1679', '1683', '1696', '1723', '1724', '1726', '1745', '1750', '1757', '1761', '1763', '1797', '1802', '1813', '1814']


In [76]:
viz.set_data(version="2")
fig = viz.accuracy_means_by_training_size()
iplot(fig)

In [77]:
fig = viz.plotUserBests()
fig.layout['title'] = "# of users whose best performance came from a particular approach"
iplot(fig)

# Experiment #3
In this experiment we compare differing amounts of personal data selected at random to combine with the impersonal 
training set as well as a cluster of the impersonal training set

In [ ]:
description = '''
Training set = WISDM v1.1
Test Set = WISDM v2.0
validation = leave-one user out, class label stratified 10-fold cross-validation within user where the training folds
are used as the pool from which we can actively sample
Sampling Methods = Least-Certain Sampling, Random Sampling
Modeling Methods = Impersonal, Sampled Personal, Sampled Personal data + All Impersonal Data, 
                    Sampled Personal Data + nearest cluster of Impersonal data,
                    Sampled Personal Data + Impersonal Data selected and weighted with Garcia-Ceja approach
'''

In [78]:
%%px --local
experiment_name3 = "experiment_09-04_train_v1_test_v2_with_random_and_least_certain/"
experiment_output_path3 = "/home/sac086/wisdm_model_personalization/results/" + experiment_name3

In [79]:
if not os.path.exists(experiment_output_path3):
    os.makedirs(experiment_output_path3)
with open(experiment_output_path3 + "README.md", "w") as fOut:
    fOut.write(description)

In [80]:
command = """wisdm.pipeline2('%s', user_ids)""" % experiment_output_path3

In [81]:
wisdm.set_data(version="2", make_compatible=True)

In [82]:
# divide the user ids up among the different cores
scatter_result = dview.scatter("user_ids", wisdm.user_ids)

start = time.time()
dview.block = True
results = dview.execute(command)
finish = time.time()
print("Finished all models in %s minutes" % ((finish - start) / 60.))

Finished all models in 44.86350203752518 minutes


### Visualize Results for Experiment #3

In [ ]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from plotly.graph_objs import *

In [ ]:
from imp import reload

In [ ]:
from wisdm import viz

In [ ]:
reload(viz)

In [83]:
results_df = viz.get_results_dataframe(experiment_output_path3)

Loading results from /home/sac086/wisdm_model_personalization/results/experiment_09-04_train_v1_test_v2_with_random_and_least_certain/
26 users loaded, 28 users excluded
These users may not have had enough data:
['1097', '1205', '1247', '1269', '1276', '1277', '1280', '1480', '1491', '1511', '1518', '1531', '1554', '1679', '1683', '1696', '1723', '1724', '1726', '1745', '1750', '1757', '1761', '1763', '1797', '1802', '1813', '1814']


In [84]:
fig = viz.accuracy_means_by_training_size()
iplot(fig)

In [85]:
fig = viz.plotUserBests()
iplot(fig)

In [86]:
wisdm.set_data(version="1", make_compatible=True)

In [87]:
len(wisdm.data_df['user'].unique())

36

In [88]:
from collections import Counter

In [90]:
data_df1 = wisdm.remove_all_nan(wisdm.data_df)

In [91]:
Counter(wisdm.data_df['class'])

Counter({b'Jogging': 1625,
         b'Sitting': 306,
         b'Stairs': 1160,
         b'Standing': 246,
         b'Walking': 2081})

# Getting IDs that did not finish

In [15]:
experiment_files = os.listdir('results/experiment_09-05_train_v1_with_random_and_least_certain/')
finished_user_ids = []
for f in experiment_files:
    if '.pickle' in f:
        finished_user_ids.append(f.split(".")[0])

In [16]:
finished_user_ids

['20',
 '33',
 '5',
 '14',
 '31',
 '19',
 '35',
 '10',
 '13',
 '11',
 '18',
 '26',
 '32',
 '34',
 '36',
 '24',
 '3',
 '8',
 '1',
 '6',
 '23',
 '22',
 '7',
 '12',
 '29',
 '15',
 '27']

In [17]:
wisdm.set_data(version="1")
unfinished_user_ids = []
for user_id in wisdm.user_ids:
    if user_id not in finished_user_ids:
        unfinished_user_ids.append(user_id)

In [18]:
unfinished_user_ids

['17', '16', '28', '4', '30', '21', '9', '25', '2']

In [19]:
np.random.choice(10, 1)

array([7])

In [ ]:
def 

In [27]:
samples = []
for stochastic_run in range(500):
    num_samples = 0
    for day in range(7):
        for hour in range(24):
            for minute in range(60):
                decision = np.random.choice(10, 1)
                if decision > 5:
                    num_samples += 1
    samples.append(num_samples)
np.mean(samples)

4031.768

In [28]:
np.std(samples)

49.439075395884984

In [22]:
(60 * 24 * 7) / 2.

5040.0